### Testing out Hyperspace on MNIST Data - Model Resiliency Test

In [4]:
from hyperspace import create_hyperspace
from ray import tune
import tensorflow as tf
from torch import nn
import pytorch_lightning as pl
from pytorch_lightning import loggers as pl_loggers
from ray.tune.suggest.skopt import SkOptSearch
from skopt import Optimizer

### Tensorflow Model Objective Function Definition

In [5]:
def mnist_tf_objective(config):
    mnist = tf.keras.datasets.mnist

    (x_train, y_train),(x_test, y_test) = mnist.load_data()
    x_train, x_test = x_train / 255.0, x_test / 255.0

    model = tf.keras.models.Sequential([
      tf.keras.layers.Flatten(input_shape=(28, 28)),
      tf.keras.layers.Dense(128, activation='relu'),
      tf.keras.layers.Dropout(config['dropout']),
      tf.keras.layers.Dense(10, activation='softmax')
    ])

    opt = tf.keras.optimizers.Adam(learning_rate=config['learning_rate'])

    model.compile(optimizer=opt,
                  loss='sparse_categorical_crossentropy',
                  metrics=['accuracy'])

    res = model.fit(x_train, y_train, epochs=config['epochs'], batch_size=config['batch_size'])
    res_test = model.evaluate(x_test, y_test)
    tune.report(test_loss = res_test[1])
    return res_test[1]

#### Run hypertune for Tensorflow Model...

In [6]:
hyperparameters = [(0.00000001, 0.1),  # learning_rate
                   (0.0, 0.9),  # dropout
                   (10, 100),  # epochs 
                   (10, 1000)]  # batch size
space = create_hyperspace(hyperparameters)

### for each space in hyperspace, we want to search the space using ray tune
i = 0
results = []
for section in space:
    # create a skopt gp minimize object
    optimizer = Optimizer(section)
    search_algo = SkOptSearch(optimizer, ['learning_rate', 'dropout', 'epochs', 'batch_size'],
                              metric='test_loss', mode='min')
    analysis = tune.run(mnist_tf_objective, search_alg=search_algo, num_samples=20, resources_per_trial={'gpu': 1})
    results.append(analysis)
    i += 1

# print out the best result
i = 0
for a in results:
    print("Best config for space "+str(i)+": "+a.get_best_config(metric="avg_test_loss"))
    i +=1

2020-10-01 10:52:59,911	INFO services.py:1164 -- View the Ray dashboard at http://127.0.0.1:8265
2020-10-01 10:53:00,996	WARNING function_runner.py:485 -- Function checkpointing is disabled. This may result in unexpected behavior when using checkpointing features or certain schedulers. To enable, set the train function arguments to be `func(config, checkpoint_dir=None)`.


(pid=67140) 2020-10-01 10:53:02.639482: W tensorflow/stream_executor/platform/default/dso_loader.cc:59] Could not load dynamic library 'libcudart.so.10.1'; dlerror: libcudart.so.10.1: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /software/openmpi-4.0.2/lib:/software/nccl/lib:/software/cuda-10.2/extras/CUPTI/lib64:/software/cuda-10.2/lib64:/usr/lib:/usr/lib64
(pid=67140) 2020-10-01 10:53:02.639519: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
(pid=67139) 2020-10-01 10:53:02.622720: W tensorflow/stream_executor/platform/default/dso_loader.cc:59] Could not load dynamic library 'libcudart.so.10.1'; dlerror: libcudart.so.10.1: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /software/openmpi-4.0.2/lib:/software/nccl/lib:/software/cuda-10.2/extras/CUPTI/lib64:/software/cuda-10.2/lib64:/usr/lib:/usr/lib64
(pid=67139) 2020-10-01 10:53:02.622754: I tens

(pid=67144) Downloading data from https://storage.googleapis.com/tensorflow/tf-keras-datasets/mnist.npz
(pid=67145) Downloading data from https://storage.googleapis.com/tensorflow/tf-keras-datasets/mnist.npz
(pid=67146) Downloading data from https://storage.googleapis.com/tensorflow/tf-keras-datasets/mnist.npz
(pid=67147) Downloading data from https://storage.googleapis.com/tensorflow/tf-keras-datasets/mnist.npz
(pid=67139) Downloading data from https://storage.googleapis.com/tensorflow/tf-keras-datasets/mnist.npz
(pid=67141) Downloading data from https://storage.googleapis.com/tensorflow/tf-keras-datasets/mnist.npz
(pid=67143) Downloading data from https://storage.googleapis.com/tensorflow/tf-keras-datasets/mnist.npz
(pid=67140) Downloading data from https://storage.googleapis.com/tensorflow/tf-keras-datasets/mnist.npz
11493376/11490434 [==============================] - 0s 0us/step


(pid=67144) 2020-10-01 10:53:04.566922: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcuda.so.1
(pid=67146) 2020-10-01 10:53:04.611202: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcuda.so.1
(pid=67145) 2020-10-01 10:53:04.614346: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcuda.so.1
(pid=67147) 2020-10-01 10:53:04.616230: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcuda.so.1
(pid=67139) 2020-10-01 10:53:04.626359: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcuda.so.1
(pid=67144) 2020-10-01 10:53:04.633788: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1716] Found device 0 with properties: 
(pid=67144) pciBusID: 0000:3d:00.0 name: Tesla V100-SXM2-32GB computeCapability: 7.0
(pid=67144) coreCloc

(pid=67144) Epoch 1/83
(pid=67145) Epoch 1/93
(pid=67147) Epoch 1/50
(pid=67141) Epoch 1/50
(pid=67143) Epoch 1/66
(pid=67140) Epoch 1/62
(pid=67139) Epoch 1/64
(pid=67146) Epoch 1/47
63/63 [==============================] - 0s 6ms/step - loss: 1.4712 - accuracy: 0.5493
(pid=67139) Epoch 2/64
65/65 [==============================] - 0s 6ms/step - loss: 1.7795 - accuracy: 0.5560
(pid=67140) Epoch 2/62
99/99 [==============================] - 0s 4ms/step - loss: 1.5949 - accuracy: 0.5221
(pid=67146) Epoch 2/47
62/62 [==============================] - 0s 6ms/step - loss: 1.2204 - accuracy: 0.6715
(pid=67147) Epoch 2/50
117/117 [==============================] - 1s 4ms/step - loss: 0.5260 - accuracy: 0.8466
(pid=67143) Epoch 2/66
116/116 [==============================] - 1s 5ms/step - loss: 0.8171 - accuracy: 0.7675
(pid=67145) Epoch 2/93
125/125 [==============================] - 1s 4ms/step - loss: 1.7349 - accuracy: 0.4460
(pid=67141) Epoch 2/50
38/62 [=================>............] -

...

74/74 [==============================] - 0s 5ms/step - loss: 1.2972 - accuracy: 0.6648
(pid=11214) Epoch 2/20
73/73 [==============================] - 0s 5ms/step - loss: 2.0941 - accuracy: 0.1981
(pid=11206) Epoch 37/46
104/104 [==============================] - 1s 5ms/step - loss: 0.5188 - accuracy: 0.8551
(pid=11224) Epoch 18/19
75/75 [==============================] - 0s 4ms/step - loss: 0.4986 - accuracy: 0.8602
(pid=10929) Epoch 54/66
130/130 [==============================] - 0s 4ms/step - loss: 0.6660 - accuracy: 0.8159
(pid=10954) Epoch 28/63
74/74 [==============================] - 0s 5ms/step - loss: 0.6508 - accuracy: 0.8005
(pid=11214) Epoch 3/20
75/75 [==============================] - 0s 4ms/step - loss: 0.4890 - accuracy: 0.8595
(pid=10929) Epoch 55/66
73/73 [==============================] - 0s 4ms/step - loss: 2.0919 - accuracy: 0.1977
(pid=11206) Epoch 38/46
104/104 [==============================] - 0s 4ms/step - loss: 0.5424 - accuracy: 0.8492
(pid=11224) Epoch 19/

(pid=11212) 2020-10-01 11:00:44.562168: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcuda.so.1
(pid=11212) 2020-10-01 11:00:44.632384: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1716] Found device 0 with properties: 
(pid=11212) pciBusID: 0000:89:00.0 name: Tesla V100-SXM2-32GB computeCapability: 7.0
(pid=11212) coreClock: 1.53GHz coreCount: 80 deviceMemorySize: 31.75GiB deviceMemoryBandwidth: 836.37GiB/s
(pid=11212) 2020-10-01 11:00:44.632731: W tensorflow/stream_executor/platform/default/dso_loader.cc:59] Could not load dynamic library 'libcudart.so.10.1'; dlerror: libcudart.so.10.1: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /software/openmpi-4.0.2/lib:/software/nccl/lib:/software/cuda-10.2/extras/CUPTI/lib64:/software/cuda-10.2/lib64:/usr/lib:/usr/lib64
(pid=11212) 2020-10-01 11:00:44.635286: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic l

75/75 [==============================] - 0s 3ms/step - loss: 0.5227 - accuracy: 0.8516
(pid=10929) Epoch 56/66
69/74 [==========================>...] - ETA: 0s - loss: 0.5982 - accuracy: 0.8199
(pid=11206) Epoch 39/46
74/74 [==============================] - 0s 4ms/step - loss: 0.5949 - accuracy: 0.8207
(pid=11214) Epoch 4/20
130/130 [==============================] - 0s 3ms/step - loss: 0.6495 - accuracy: 0.8180
(pid=10954) Epoch 29/63
75/75 [==============================] - 0s 3ms/step - loss: 0.5343 - accuracy: 0.8407
(pid=10929) Epoch 57/66
73/73 [==============================] - 0s 4ms/step - loss: 2.0970 - accuracy: 0.2023
(pid=11206) Epoch 40/46
74/74 [==============================] - 0s 5ms/step - loss: 0.5768 - accuracy: 0.8270
(pid=11214) Epoch 5/20
13/74 [====>.........................] - ETA: 0s - loss: 0.5650 - accuracy: 0.8292
(pid=11212) Epoch 1/14
75/75 [==============================] - 0s 3ms/step - loss: 0.5385 - accuracy: 0.8429
(pid=10929) Epoch 58/66
130/130 [=

(pid=11211) 2020-10-01 11:00:46.751148: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcuda.so.1
(pid=11211) 2020-10-01 11:00:46.820202: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1716] Found device 0 with properties: 
(pid=11211) pciBusID: 0000:3e:00.0 name: Tesla V100-SXM2-32GB computeCapability: 7.0
(pid=11211) coreClock: 1.53GHz coreCount: 80 deviceMemorySize: 31.75GiB deviceMemoryBandwidth: 836.37GiB/s
(pid=11211) 2020-10-01 11:00:46.820455: W tensorflow/stream_executor/platform/default/dso_loader.cc:59] Could not load dynamic library 'libcudart.so.10.1'; dlerror: libcudart.so.10.1: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /software/openmpi-4.0.2/lib:/software/nccl/lib:/software/cuda-10.2/extras/CUPTI/lib64:/software/cuda-10.2/lib64:/usr/lib:/usr/lib64
(pid=11211) 2020-10-01 11:00:46.822969: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic l

73/73 [==============================] - 0s 4ms/step - loss: 2.0559 - accuracy: 0.2141
(pid=11206) Epoch 46/46
61/61 [==============================] - 0s 5ms/step - loss: 1.7390 - accuracy: 0.3548
(pid=11212) Epoch 5/14
75/75 [==============================] - 0s 4ms/step - loss: 0.5272 - accuracy: 0.8482
(pid=10929) Epoch 65/66
130/130 [==============================] - 0s 3ms/step - loss: 0.6879 - accuracy: 0.8103
(pid=10954) Epoch 34/63
74/74 [==============================] - 0s 6ms/step - loss: 0.5480 - accuracy: 0.8401
(pid=11214) Epoch 11/20
75/75 [==============================] - 0s 4ms/step - loss: 0.5126 - accuracy: 0.8488
(pid=10929) Epoch 66/66
61/61 [==============================] - 0s 6ms/step - loss: 1.7418 - accuracy: 0.3563
(pid=11212) Epoch 6/14
 1/61 [..............................] - ETA: 0s - loss: 1.7302 - accuracy: 0.3410
(pid=10929)  - ETA: 0s - loss: 0.4671 - accuracy: 0.8438
11/61 [====>.........................] - ETA: 0s - loss: 1.7643 - accuracy: 0.3440


### Pytorch Model Objective Function Definition

In [ ]:
class NumberNet(pl.LightningModule):
    def __init__(self, config):
        super().__init__()
        self.model = nn.Sequential(
            nn.Flatten(), 
            nn.Linear(784, 128), 
            nn.ReLU(), 
            nn.Dropout(config['dropout']), 
            nn.Linear(128, 10), 
            nn.Softmax())
        self.criterion = nn.CrossEntropyLoss()
        self.config = config
        self.test_loss = None
    
    def train_dataloader(self):
        return torch.utils.data.DataLoader(torchvision.datasets.MNIST("~/resiliency/", train=True, 
                                                                      transform=torchvision.transforms.ToTensor(), target_transform=None, download=True), 
                                           batch_size=config['batch_size'])
    
    def test_dataloader(self):
        return torch.utils.data.DataLoader(torchvision.datasets.MNIST("~/resiliency/", train=True, 
                                                                      transform=torchvision.transforms.ToTensor(), target_transform=None, download=True), 
                                           batch_size=config['batch_size'])
    
    def configure_optimizers(self):
        optimizer = torch.optim.Adam(self.parameters(), lr=config['learning_rate'])
        return optimizer
    
    def forward(self, x):
        return self.model(x)
    
    def training_step(self, train_batch, batch_idx):
        x, y = train_batch
        logits = self.forward(x)
        loss = self.criterion(logits, y)
        logs = {'train_loss': loss}
        return {'loss': loss}
    
    def test_step(self, test_batch, batch_idx):
        x, y = test_batch
        logits = self.forward(x)
        loss = self.criterion(logits, y)
        logs = {'test_loss': loss}
        return {'loss': loss}
    
    def test_epoch_end(self, outputs):
        loss = []
        for x in outputs:
            loss.append(float(x['test_loss']))
        avg_loss = statistics.mean(loss)
        tensorboard_logs = {'test_loss': avg_loss}
        self.test_loss = avg_loss
        return {'avg_test_loss': avg_loss, 'log': tensorboard_logs}


In [ ]:
def mnist_pt_objective(config):
    model = NumberNet(config)
    trainer = pl.Trainer(max_epochs=config['epochs'])
    trainer.fit(model)
    trainer.test(model)
    tune.report(test_loss=model.test_loss)
    return model.test_loss